# Finding natural geroprotectors with Precious3GPT and BATMAN

This notebook will teach you how to use P3GPT to emulate the workflow of a chemical screening projects.

In particular, we will identify the compounds encountered in traditional Chinese medicine (TCM) with a geroprotective potential.

In this notebook, we generate omics signatures in 8 human tissues. We will then use these signatures and an external catalog of TCM ingredients [BATMAN](http://bionet.ncpsb.org.cn/batman-tcm/#/browse) to select the compounds that target the genes in P3GPT-generated signatures.

<center><img src="https://huggingface.co/datasets/f-galkin/batman2/resolve/main/demo/imgs/experiment_scheme.png" width="800" ></center>
<center><i>This notebook only focuses on TCM compounds with known targets, but you may modify the code to look for geroprotectors based on the information about predicted targets as well. In this case, the identified potential geroprptectors will be more numerous and might contain novel compounds.</i></center>


> ⚠️ **Dependency:** To replicate this project, you need to download some files from [Precious3GPT's repo](https://doi.org/10.57967/hf/2699) and then move the ```mpt_7b``` directory and ```precious3_gpt_multi_modal.py``` from `p3-mm` to `~/P3LIB/`. You can remove all the other downloaded files.

``` python
from huggingface_hub import snapshot_download
snapshot_download(repo_id="insilicomedicine/precious3-gpt-multi-modal", local_dir='./p3-mm')
```
> In the end, your directory structure should look as follows:
```
└── demo
    ├── 1Aug2024_aging_signatures.pckl [optional]
    ├── HF_TCM+P3GPT_sceening.ipynb
    ├── P3GPT_compound_targets.pckl
    └── P3LIB
        ├── mpt_7b
        │   ├── ...
        │   └── ...
        ├─ endpoints.py
        ├─ formula_picker.py
        └─ precious3_gpt_multi_modal.py
```

In [1]:
from typing import Dict, List, Any
import os
import torch
from transformers import AutoTokenizer, AutoModel
import pandas as pd
import time
import numpy as np
from transformers import GenerationConfig
import pickle
import numpy as np
import pandas as pd
from scipy.stats import fisher_exact

from P3LIB.endpoints import EndpointHandler

## 1. Generate aging signatures

Define the tissues and the omics domains to be screened to be inserted in the P3GPT prompt template.

Since we are only intereseted in aging-related omics differences, we only need one instruction: `age_group2diff2age_group`.
Make sure to specify the case and control age groups exactly as specified in the `p3_entities_with_type.csv` file.

We can leave most other prompt fields empty but you are free to modify them and thus reproduce a different setting. E.g. you can leave `tissue` vacant and fill in the `cell` field to enable an *in vitro* setting, or you can specify the `drug` to explore how a compound affects the aging signature.

In [2]:
tissue_options = ['skin', 'muscle', 'whole blood', 'epithelium', 'artery', 'fat tissue', 'brain', 'liver']
domain_options = ['methylation', 'proteomics', 'expression']

prompt_config_age = {
        "instruction": 'age_group2diff2age_group',
        "tissue": '', #insert tissue here
        "age": "",
        "cell": "", #insert cell line here
        "efo": "",
        "datatype": "",
        "drug": "", #insert cpd here if any
        "dose": "",
        "time": "",
        "case": "70.0-80.0",
        "control": "19.95-25.0",
        "dataset_type": "", #insert domain here
        "gender": "",
        "species": "human",
        "up": [],
        "down": []
    }

The `endpoints.py` module contains several options to invoke P3GPT.
Unless your input prompt contains lists of up-/down-regulated genes, it is advised to use `EndpointHandler` for local inference.

The only parameter you need to specify at handler initialization is the GPU device to deploy P3GPT on.

In [3]:
handler = EndpointHandler(device='cuda:2')

/home/f.galkin/.cache/huggingface/modules/transformers_modules/mosaicml/mpt-7b/039e37745f00858f0e01e988383a8c4393b1a4f5/configuration_mpt.py:114: UserWarning: alibi or rope is turned on, setting `learned_pos_emb` to `False.`
  warnings.warn(f'alibi or rope is turned on, setting `learned_pos_emb` to `False.`')
/home/f.galkin/.cache/huggingface/modules/transformers_modules/mosaicml/mpt-7b/039e37745f00858f0e01e988383a8c4393b1a4f5/configuration_mpt.py:141: UserWarning: If not using a Prefix Language Model, we recommend setting "attn_impl" to "flash" instead of "triton".
  warnings.warn(UserWarning('If not using a Prefix Language Model, we recommend setting "attn_impl" to "flash" instead of "triton".'))


With 8 tissues and 3 omics domains, you will generate a total of 24 aging signatures.

The default mode of execution for P3GPT is prompt completion, which is inherently stocahstic. To avoid any sampling effects, we enabled a special mode of P3GPT execution in `EndpointHandler`. Instead of generating gene tokens one at a time, we access the complete output probability distribution for up- and down-regulated genes and take top-N tokens from them.

We can treat a gene's output probability as a proxy for its importance in the aging process to be used later.

In [7]:
generations = {z:{x:{y:[] for y in ('up', 'down')}for x in domain_options} for z in tissue_options}
for tis in generations:
    prompt_config_age['tissue'] = tis
    for dom in generations[tis]:
        print(f"Running generations for {tis}-{dom}")
        prompt_config_age['dataset_type'] = dom
        for direct in generations[tis][dom]:
            # uses the get_gene_probabilities method to get a list of top-k genes by their output probability
            try:
                generations[tis][dom][direct] = handler.get_gene_probabilities(prompt_config=prompt_config_age, top_k=100, list_type=direct,
                                                                               random_seed = 137)
            except ValueError:
                # invoke P3GPT with a non-default random seed in case you encounter any errors in your generation
                generations[tis][dom][direct] = handler.get_gene_probabilities(prompt_config=prompt_config_age, top_k=100, list_type=direct,
                                                                               random_seed = 138)

Running generations for skin-methylation
[BOS]<age_group2diff2age_group><tissue>skin </tissue><cell></cell><efo></efo><datatype></datatype><drug></drug><dose></dose><time></time><case>70.0-80.0 </case><control>19.95-25.0 </control><dataset_type>methylation </dataset_type><gender></gender><species>human </species><up>


/home/f.galkin/.cache/huggingface/modules/transformers_modules/mosaicml/mpt-7b/039e37745f00858f0e01e988383a8c4393b1a4f5/attention.py:87: UserWarning: Propagating key_padding_mask to the attention module and applying it within the attention module can cause unnecessary computation/memory usage. Consider integrating into attn_bias once and passing that to each attention module instead.
  warnings.warn('Propagating key_padding_mask to the attention module ' + 'and applying it within the attention module can cause ' + 'unnecessary computation/memory usage. Consider integrating ' + 'into attn_bias once and passing that to each attention ' + 'module instead.')


This is token index where gene should be predicted:  1
[BOS]<age_group2diff2age_group><tissue>skin </tissue><cell></cell><efo></efo><datatype></datatype><drug></drug><dose></dose><time></time><case>70.0-80.0 </case><control>19.95-25.0 </control><dataset_type>methylation </dataset_type><gender></gender><species>human </species>
This is token index where gene should be predicted:  260
Running generations for skin-proteomics
[BOS]<age_group2diff2age_group><tissue>skin </tissue><cell></cell><efo></efo><datatype></datatype><drug></drug><dose></dose><time></time><case>70.0-80.0 </case><control>19.95-25.0 </control><dataset_type>proteomics </dataset_type><gender></gender><species>human </species><up>
This is token index where gene should be predicted:  1
[BOS]<age_group2diff2age_group><tissue>skin </tissue><cell></cell><efo></efo><datatype></datatype><drug></drug><dose></dose><time></time><case>70.0-80.0 </case><control>19.95-25.0 </control><dataset_type>proteomics </dataset_type><gender></ge

### ↓ This file stores the generated up-down lists for aging tissues

In [6]:
with open('./1Aug2024_aging_signatures.pckl', 'wb') as f:
    pickle.dump(generations,f)

> 💡 **Note**: You may load the file above directly to skip step-1 and use P3GPT-generated aging signature in your TCM research
```python
with open('./1Aug2024_aging_signatures.pckl', 'rb') as f:
    generations = pickle.load(f)
```

## 2. Screen TCM compounds

The file below contains 659 TCM ingredients that are represented in the P3GPT training set.

The BATMAN catalog refers to compounds by Pubchem CIDs while P3GPT uses conventional names, so we created a mapping CID→Names.
BATMAN also specifies protein targets the compounds are known or predicted to affect. We will measure the overlap between these lists and the P3GPT-generated aging signatures to find the most promising compounds. 

In [9]:
with open('./P3GPT_compound_targets.pckl', 'rb') as f:
    TCM_cpds = pickle.load(f)

In [10]:
# See what an entry in the mapping looks like
list(TCM_cpds.items())[0]

(5281792,
 {'title': 'rosmarinic-acid',
  'known_targets': {'symbols': ['C5', 'CCR3', 'CCL2', 'PREP', 'NFKB1',
                                'IKBKB', 'CASP3', 'C3', 'OLIG2', 'CCL11', 
                                'CD86', 'AURKA', 'IL2', 'F2', 'IDO1',
                                'IL4', 'RPS6KB1','ABAT', 'CCL3','STAT1',
                                'CD80', 'IL5', 'IL6'],
                    'entrez_ids': [18, 3565, 4790, 836, 3551,
                                   3620, 6772, 718, 2147, 3558,
                                   3569, 6347, 6356, 727, 6790,
                                   3567, 942, 6348, 10215, 6198,
                                   5550, 1232, 941]},
  'predicted_targets': {'symbols': ['IFNG', 'PTGS1', 'PTGS2', 'TPMT'],
  'entrez_ids': [3458, 5742, 5743, 7172]}})

Next, let's count how many times each compound's targets pop up in the generated signatures. To see if the overlap between targets and important aging genes is significant, we'll apply Fisher's exact test. As the background set, we shall use the total number of genes used by P3GPT — 25,332. 

In [20]:
list_len = 100
enrich_stats = pd.DataFrame(None, index = None,
                            columns = ['compound', 'cid', 'tissue', 'domain',
                                       'p_value', 'target_type', 'N_targets',
                                       'hit_targets'])
for cid in TCM_cpds:
    tg_sets = {'known':set(TCM_cpds[cid]['known_targets']['symbols']),
              "predicted":set(TCM_cpds[cid]['predicted_targets']['symbols'])}
    tg_sets["both"] = tg_sets['known'] | tg_sets['predicted']
    for tis in generations:
        for dom in generations[tis]:
            p3_set = set(generations[tis][dom]['up'][:list_len] + generations[tis][dom]['down'][:list_len])
            for tg_type, tg_set in tg_sets.items():
                p3_hits = tg_set & p3_set
                # cols: in targets, not in targets
                # rows: in P3 output, not in P3 output
                cont_table = (a := np.array([[len(p3_hits), len(tg_set - p3_hits)],
                                                  [len(p3_hits - tg_set), 0]])) + \
                                  np.array([[0, 0],
                                            [0, 25332 - a.sum().sum()]])

                F_exact = fisher_exact(table=cont_table, alternative='greater')
                #['compound', 'tissue', 'domain', 'p_value', 'target_type']
                enrich_stats.loc[enrich_stats.shape[0],:] = [TCM_cpds[cid]['title'],
                                                             cid,
                                                             tis,
                                                             dom,
                                                             F_exact[1],
                                                             tg_type,
                                                             len(tg_set),
                                                             len(p3_hits)]

In [21]:
print(f"Total number of tests: {enrich_stats.shape[0]}")

Total number of tests: 47448


Since we have run thousands of statistical tests, it makes sense to include a multiple comparison correction

In [22]:
enrich_stats["corr_Pv"] = [min(1, x) for x in enrich_stats["p_value"] * enrich_stats.shape[0]]
enrich_stats = enrich_stats[enrich_stats["corr_Pv"]<.001]
print(f"Remaining entries: {enrich_stats.shape[0]}")
print(f'Compounds that passed 1+ enrichment tests: {len(enrich_stats.compound.unique())}')

Remaining entries: 8866
Compounds that passed 1+ enrichment tests: 424


We can now zoom in on the compounds that passed the test.

Out of all 659 TCM compounds, the targets of 424 of them significantly overlapped with an aging aging signature.
Let's trim the table of significant enrichments even further by considering only the documented targets. 

> 💡 **Note:** You may choose a different target confirmation level. Looking for enrichment in known targets creates a bias toward well-studied compounds. Such popular anti-aging compounds as curcumin, for example, have thousands of publications covering their cellular interactions. Meanwhile, an obscure but an equally potent geroprotector may have zero known targets. Repeating this workflow with predicted targets is likely to provide more novel compounds.

In [23]:
confirmation_level = 'known'
enrich_stats = enrich_stats[enrich_stats["target_type"]==confirmation_level]
print(f"Remaining entries: {enrich_stats.shape[0]}")
print(f'Compounds that passed 1+ enrichment tests: {len(enrich_stats.compound.unique())}')

Remaining entries: 375
Compounds that passed 1+ enrichment tests: 80


80 compounds is a much more manageable compound selection.

These TCM compounds are targetting the genes involved in aging and may be considered for futher investigation *in vitro* or *in vivo*.
But what if we we wanted to compose a cocktail of TCM ingredients that will slow down the aging processes in as many tissues as possible?
Are there any TCM compounds that have been detected in 8/8 tissues?


In [32]:
cpd_counts = {}
print("--- N potential geroprotectors identified in each tissue ---")
for t in tissue_options:
    tis_df = enrich_stats[(enrich_stats.tissue == t)& \
                          (enrich_stats.target_type == confirmation_level)]
    print(f'N {t}-compounds = {len(tis_df.compound.unique())}')
    for cpd in tis_df.compound.unique():
        if cpd not in cpd_counts:
            cpd_counts[cpd] = 0
        cpd_counts[cpd]+=1

cpds_by_tis_count = dict()
for i in range(1,9):
    cpds_by_tis_count[i] = [x for x,y in cpd_counts.items() if y == i]

for i in (6,7,8):
    print(f"\n--- TCM ingredients targeting aging in {i} tissues (N = {len(cpds_by_tis_count[i])}) ---")
    print(*cpds_by_tis_count[i], sep ='\n')
    


--- N potential geroprotectors identified in each tissue ---
N skin-compounds = 38
N muscle-compounds = 25
N whole blood-compounds = 48
N epithelium-compounds = 19
N artery-compounds = 32
N fat tissue-compounds = 17
N brain-compounds = 47
N liver-compounds = 23

--- TCM ingredients targeting aging in 6 tissues (N = 4) ---
alpha-tocopherol
capsaicin
baicalin
testosterone

--- TCM ingredients targeting aging in 7 tissues (N = 2) ---
kaempferol
triptolide

--- TCM ingredients targeting aging in 8 tissues (N = 8) ---
colchicine
quercetin
apigenin
resveratrol
curcumin
brd-k55591206;epigallocatechin 3-gallate
estradiol
progesterone


A total of 14 compounds were detected as potential geroprotectors in 6+ tissues, while almost half of all detected ingredients affect agig only in one tissue.
Among them, 8 were targetting the aging signatures in 8/8 tissues. 

<center><img src="https://huggingface.co/datasets/f-galkin/batman2/resolve/main/demo/imgs/cpds_affecting_tissue_aging.svg" width="600" ></center>

> 💡 **Note:** The compounds we call "potential geroprotectors" may in fact accelerate aging. When we difined important aging genes, we did binned the up- and down-regulated genes together, although the directionality of change is extremely important in this setting. Additionally, the mechanism of action (agonist/antagonist) of a TCM ingredient needs to be taken into account. We can lean on the fact that most compounds in BATMAN are generally considered safe or even beneficial to the organism, but ultimately, the final list of TCM geroprotectors needs to be manually reviewed.

## 3. Selecting a TCM formula

Now that we have a list of 14 compounds with a systemic effect on aging, we can leverage BATMAN to do either of the following:

- Screen existing TCM formulas to find those that contain as many compounds from our list as possible;
- Make a new TCM formula ourselves by selecting herbs one by one.

We will demonstrate only the former option in this notebook.

In [38]:
# Here are the CIDs of the potential geroprotectors 
# we identified in section 2
cids = [969516, #curcumin
        445154, #resveratrol
        5280343, #quercetin
        6167, #colchicine
        5280443, #apigening
        65064, #EGCG3
        5757, # estradiol
        5994, # progesterone
        5280863, # kaempferol
        107985, # triptolide
        14985, #alpha-tocopherol
        1548943, # Capsaicin
        64982, # Baicalin
        6013, # Testosterone
        ]

For the sake of brevity, we have externalized the scripts used to parse BATMAN files into linked lists of ingredients-herbs-formulas with the `formula_picker.py` mini module available at the [batman2](https://huggingface.co/datasets/f-galkin/batman2) dataset repository. 

Feel free reuse the scripts and files we prepared in your own TCM-related projects. If you don't need our `TCMDB` wrapper class, you can access BATMAN data tables directly by executing the following commands:
```python
from datasets import load_dataset
batman_ingredients = load_dataset("f-galkin/batman2", "batman_ingredients")
batman_herbs = load_dataset("f-galkin/batman2", "batman_herbs")
batman_formulas = load_dataset("f-galkin/batman2", "batman_formulas")
```

In [34]:
from P3LIB.formula_picker import TCMDB
from datasets import load_dataset
db = TCMDB.download_from_hf()

We formatted the BATMAN files (accessed on 8/1/2024) to support basic search operations, such as looking up a TCM formula that has the maximum amount of the compounds provided in a query.

In [41]:
p3_formula = db.select_formula_by_cpd(cids)
print("%s compounds of 14 are encountered in the following TCM formulas:\n%s"%p3_formula)

13 compounds of 14 are encountered in the following TCM formulas:
['ZHANG ZHOU SHEN QU']


Not a single TCM formula out of the 54,832 described in BATMAN2 has all the 14 potential geroprotectors we selected.
And only 1 formula has 13/14 compounds — ZHANG ZHOU SHEN QU. Let's take a closer look at it.

In [45]:
pinyin_name = 'ZHANG ZHOU SHEN QU'
print(f'The contents of the {pinyin_name} ({db.formulas[pinyin_name].synonyms[0]}) TCM formula')
for i, herb in enumerate(db.formulas[pinyin_name].herbs):
    print(f"{i+1}. {herb.synonyms[2]} ({herb.synonyms[1]})")


The contents of the ZHANG ZHOU SHEN QU (漳州神曲) TCM formula
1. Weeping forsythia (连翘)
2. Tsaoko (草果)
3. Yerbadetajo (墨旱莲)
4. Haichow elsholtzia (香薷)
5. Common anemarrhena (知母)
6. Medicine terminalia equivalent plant: terminalia chebula var tomentella (诃子)
7. Slenderstyle acanthopanax root-bark equivalent plant:  acanthopanax sessiliflorus ,  acanthopanax senticosus (五加皮)
8. Dried tangerine peel (陈皮)
9. Bark of officinal magnolia (厚朴)
10. Perilia fruit (紫苏子)
11. Oriental waterplantain (泽泻)
12. Chinese hawthorn equivalent plant: crataegus pinnatifida  var major (山楂)
13. Common hogfennel equivalent plant:  peucedanum praeruptorum ,  peucedanum longshengens,  peucedanum rubricaule , ligusticum brachylobum (前胡)
14. Glabrous greenbrier equivalent plant: smilax menispermoidea (土茯苓)
15. Chinese star anise (八角茴香)
16. White mulberry branch (桑枝)
17.  (槟榔)
18. Wild mint (薄荷)
19. Pummelo peel (化橘红)
20. Mongolian snakegourd root (天花粉)
21. Red peony root (赤芍)
22. Grassleaved sweetflag equivalent plant:

The formula we ended up with is quite complex and contains 75 herbal components, such as nutmeg, turmeric, scutellaria, citrus peels, patchouli and others.

You can learn more about this composition on other [TCM databases](https://bidd.group/TCMID/tcmf.php?formula=TCMFx6833). For now, that is where we shall conclude our search